In [1]:
from sklearn.compose import ColumnTransformer
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, OrdinalEncoder
from sklearn.ensemble import RandomForestClassifier
from sklearn.impute import SimpleImputer
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
import numpy as np
from sklearn.model_selection import GridSearchCV
import sys

import dice_ml
from dice_ml import Dice
from dice_ml.utils import helpers  # helper functions
%load_ext autoreload
%autoreload 2
Ncount=1

In [2]:
import pandas as pd
pathCSV = 'dataset.csv'
dataset = pd.read_csv(pathCSV, sep=',')
headers = dataset.columns.tolist()
dataset = dataset[headers[2:-5]]
target = dataset[headers[-6]]

In [3]:
categorical_features = ['Type']
numeric_features = ['Air temperature [K]','Process temperature [K]','Rotational speed [rpm]','Torque [Nm]','Tool wear [min]']

numeric_transformer = Pipeline(steps=[
                                      ('imputer', SimpleImputer(strategy='median')),
                                      ('scaler', StandardScaler())])

categorical_transformer = Pipeline(steps=[
                                          ('imputer', SimpleImputer(strategy='constant', fill_value='missing')),
                                          ('label', OrdinalEncoder())
                                          ])  

preprocessor = ColumnTransformer(
                                 transformers=[
                                                ('cat', categorical_transformer, categorical_features),
                                               ('num', numeric_transformer, numeric_features),
                                               ])

model_reg = ['nb'
                'dt',
                'rf',
                'gbc']


param_nb = {'var_smoothing': np.logspace(0,-9, num=10)}

param_dt = [{'max_depth': [5,10,20]}]

param_rf = [{'bootstrap': [True, False],
                 'max_depth': [10, 20],
                 'max_features': ['auto', 'sqrt'],
                 'min_samples_leaf': [1, 2, 4],
                 'min_samples_split': [2],}]

param_gbc = [{'learning_rate': [0.01,0.03],
                'subsample'    : [0.5, 0.2],
                'n_estimators' : [100,200],
                'max_depth'    : [4,8]}]

models_classification = {
        'nb': {'name': 'Naive Bayes',
               'estimator': GaussianNB(),
               'param': param_nb,
              },
        'dt': {'name': 'Decision Tree',
               'estimator': DecisionTreeClassifier(random_state=42),
               'param': param_dt,
              },
        'rf': {'name': 'Random Forest',
               'estimator': RandomForestClassifier(random_state=42),
               'param': param_rf,
              },

        'gbc': {'name': 'Gradient Boosting Regressor',
                'estimator': GradientBoostingClassifier(random_state=42),
                'param': param_gbc
                },
    }

mlModel = 'rf'

mod_grid = GridSearchCV(models_classification[mlModel]['estimator'], models_classification[mlModel]['param'], cv=5, return_train_score = False, scoring='f1_macro', n_jobs = 8)
model = Pipeline(steps=[('preprocessor', preprocessor),
                ('classifier', mod_grid)])

datasetP = preprocessor.fit_transform(dataset[headers[2:-6]])
datasetP = pd.DataFrame(datasetP, columns=headers[2:-6])
datasetP[headers[-6]]= dataset[headers[-6]]
datasetX = dataset.drop(headers[-6], axis=1)
x_train, x_test, y_train, y_test = train_test_split(datasetX,
                                                    target,
                                                    test_size=0.2,
                                                    random_state=0,
                                                    stratify=target)
model.fit(x_train, y_train)
d = dice_ml.Data(dataframe=dataset, continuous_features=numeric_features, outcome_name=headers[-6])
m = dice_ml.Model(model=model, backend="sklearn")

c:\Users\utente\AppData\Local\Programs\Python\Python310\lib\site-packages\sklearn\ensemble\_forest.py:427: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features='sqrt'` or remove this parameter as it is also the default value for RandomForestClassifiers and ExtraTreesClassifiers.
  warn(


In [4]:
dataset.head()

Type  Air temperature [K]  Process temperature [K]  Rotational speed [rpm]  \
0    M                298.1                    308.6                    1551   
1    L                298.2                    308.7                    1408   
2    L                298.1                    308.5                    1498   
3    L                298.2                    308.6                    1433   
4    L                298.2                    308.7                    1408   

   Torque [Nm]  Tool wear [min]  Machine failure  
0         42.8                0                0  
1         46.3                3                0  
2         49.4                5                0  
3         39.5                7                0  
4         40.0                9                0

In [5]:
exp = Dice(d, m, method="random")
constraints={}
desc=x_train.describe()
for i in numeric_features:
    constraints[i]=[desc[i]['min'],desc[i]['max']]
e1 = exp.generate_counterfactuals(x_test, total_CFs=Ncount, desired_range=None,
                                  desired_class="opposite",
                                  permitted_range=constraints, features_to_vary="all")
#e1.visualize_as_dataframe(show_only_changes=True)

100%|██████████| 2000/2000 [06:22<00:00,  5.22it/s]


In [11]:
data = []
for cf_example in e1.cf_examples_list:
    data.append(cf_example.final_cfs_df)

df_combined = pd.concat(data, ignore_index=True)
df1 = pd.DataFrame(preprocessor.transform(df_combined),columns=headers[2:-6])
df1[headers[-6]]= df_combined[headers[-6]]
df2 = pd.DataFrame(preprocessor.transform(x_test),columns=headers[2:-6])
df_combined = df1
x_test = df2
for i in range(len(df_combined)):
    df_combined[headers[2]].iloc[i] = 1 if df_combined[headers[2]].iloc[i]!= x_test[headers[2]].iloc[i] else 0
    df_combined[headers[3:-6]].iloc[i] = df_combined[headers[3:-6]].iloc[i] - x_test[headers[3:-6]].iloc[i//Ncount]
    df_combined[headers[-6]].iloc[i] = df_combined[headers[-6]].iloc[i] - y_test.iloc[i//Ncount]
df_combined.to_csv(path_or_buf=f'{mlModel}/dice/counterfactuals.csv', index=False, sep=',')
df_combined.dtypes
df_filtered = df_combined[df_combined[headers[-6]] != 0]
count_per_column = df_filtered.apply(lambda x: (x != 0).sum())
diff_per_column = df_filtered.apply(lambda x: (abs(x)).sum())
#relative_per_column = df_filtered.apply(lambda x: (abs(x)/abs(df_filtered[headers[-6]])/(x != 0)).sum())

original_stdout = sys.stdout
with open(f'{mlModel}/dice/count.txt', 'w') as f:
    sys.stdout = f
    print('\n--------------------- Counterfactual absolute counts:-------------------------')
    print(diff_per_column)
    print('\n--------------------- Counterfactual relative counts:-------------------------')
    print(diff_per_column/count_per_column)
            
        
sys.stdout = original_stdout

C:\Users\utente\AppData\Local\Temp\ipykernel_19028\2542605129.py:12: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df_combined[headers[2]].iloc[i] = 1 if df_combined[headers[2]].iloc[i]!= x_test[headers[2]].iloc[i] else 0
C:\Users\utente\App